In [ ]:
#@markdown Build a dataset from ALL images in /content/ with EXIF metadata (using exiftool) as separate columns and WebM files, saving to Google Drive

# Step 1: Install required libraries and exiftool
!pip install Pillow imageio[ffmpeg] datasets pandas
!apt-get update && apt-get install -y libimage-exiftool-perl

# Step 2: Import required libraries
import os
import glob
import subprocess
from PIL import Image
import imageio.v3 as iio
import pandas as pd
from datasets import Dataset, Features, Image as HFImage, Value
from google.colab import drive

# Step 3: Mount Google Drive
drive.mount('/content/drive')
output_dir = '/content/drive/My Drive/exif_dataset' #@param {type:'string'}

# Step 4: Define function to extract metadata using exiftool
def get_exif_data(image_path):
    try:
        # Run exiftool to extract all metadata as JSON
        result = subprocess.run(
            ['exiftool', '-j', image_path],
            stdout=subprocess.PIPE,
            stderr=subprocess.PIPE,
            text=True,
            check=True
        )
        # Parse JSON output (exiftool -j returns a list of dictionaries)
        metadata = eval(result.stdout)[0]  # First item in the list
        return metadata
    except subprocess.CalledProcessError as e:
        print(f"exiftool error for {image_path}: {e.stderr}")
        return {"Error": f"exiftool failed: {str(e)}"}
    except Exception as e:
        return {"Error": f"Failed to read metadata: {str(e)}"}

# Step 5: Define function to convert image to WebM
def convert_to_webm(image_path, output_path):
    try:
        img = iio.imread(image_path)
        iio.imwrite(output_path, img, codec='vp8', fps=1, quality=8)
        return True
    except Exception as e:
        print(f"Error converting {image_path} to WebM: {str(e)}")
        return False

# Step 6: Collect ALL images from /content/
image_dir = "/content/"
image_extensions = ["*.jpg", "*.jpeg", "*.png"]
image_paths = []
for ext in image_extensions:
    image_paths.extend(glob.glob(os.path.join(image_dir, ext)))

if not image_paths:
    print("No images found in /content/")
else:
    # Step 7: Process all images to collect metadata keys and data
    images = []
    webm_paths = []
    metadata_list = []
    all_metadata_keys = set()

    for img_path in image_paths:
        print(f"\nProcessing {img_path}:")

        # Load image
        try:
            img = Image.open(img_path).convert('RGB')
        except Exception as e:
            print(f"Error loading image {img_path}: {str(e)}")
            continue

        # Extract metadata with exiftool
        metadata = get_exif_data(img_path)
        print("Metadata (via exiftool):")
        for key, value in metadata.items():
            print(f"  {key}: {value}")
            all_metadata_keys.add(key)  # Collect unique metadata keys

        # Convert to WebM
        webm_path = os.path.splitext(img_path)[0] + ".webm"
        if convert_to_webm(img_path, webm_path):
            print(f"  Saved WebM: {webm_path}")
            images.append(img)
            webm_paths.append(webm_path)
            metadata_list.append(metadata)
        else:
            print(f"  Skipped WebM conversion for {img_path}")
            continue

    # Step 8: Check if any images were processed
    if not images:
        print("No images were successfully processed.")
    else:
        # Step 9: Prepare dataset dictionary with separate columns for each metadata key
        data_dict = {'image': images, 'webm_path': webm_paths}

        # Initialize columns for each metadata key with None
        for key in all_metadata_keys:
            data_dict[key] = [None] * len(images)

        # Populate metadata values
        for i, metadata in enumerate(metadata_list):
            for key, value in metadata.items():
                data_dict[key][i] = str(value)  # Convert values to strings

        # Step 10: Define dataset features
        features = Features({
            'image': HFImage(),
            'webm_path': Value("string"),
            **{key: Value("string") for key in all_metadata_keys}  # Dynamic columns for metadata keys
        })

        # Step 11: Create Hugging Face Dataset
        dataset = Dataset.from_dict(data_dict, features=features)

        # Step 12: Verify the dataset
        print("\nDataset Summary:")
        print(dataset)
        if len(dataset) > 0:
            print("\nExample of accessing first item:")
            print("WebM Path:", dataset['webm_path'][0])
            print("Image type:", type(dataset['image'][0]))
            print("Image size:", dataset['image'][0].size)
            print("Metadata columns (first item):")
            for key in all_metadata_keys:
                if dataset[key][0] is not None:
                    print(f"  {key}: {dataset[key][0]}")

        # Step 13: Save dataset to Google Drive
        try:
            os.makedirs(output_dir, exist_ok=True)
            dataset.save_to_disk(output_dir)
            print(f"\nDataset saved to {output_dir}")
        except Exception as e:
            print(f"Error saving dataset to Google Drive: {str(e)}")